using resnet: now let's try 100 epochs but this time save the training loss. now let's try 10 fold

In [1]:
import os
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import pandas as pd
from tensorflow import keras
from keras.models import Sequential
from keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, Dropout, Activation, BatchNormalization
from keras.optimizers import Adam
from keras.metrics import categorical_crossentropy
from keras.preprocessing.image import ImageDataGenerator
from sklearn.metrics import precision_recall_fscore_support, confusion_matrix
import pickle
import matplotlib.pyplot as plt
import os
from keras.applications import ResNet50

# Paths to the base directory containing all folds
base_data_dir = '/home/wangg/REU-Hearing-Loss-Project-1/machine learning/allFolds/10folds - 80-20 train test split (includes all subjects)'

# Image dimensions
img_height, img_width = 224, 224

# Define batch size
batch_size = 32
for fold_number in range(7, 11):
    # Paths to training and testing data for the current fold
    training_data_path = os.path.join(base_data_dir, f'fold{fold_number}/Training')
    testing_data_path = os.path.join(base_data_dir, f'fold{fold_number}/Testing')

    # Create data generators for training and testing with data augmentation
    train_datagen = ImageDataGenerator(
        rescale=1./255,
        horizontal_flip=True,
        rotation_range=20,
        width_shift_range=0.2,
        height_shift_range=0.2,
        shear_range=0.2,
        zoom_range=0.2
    )
    # Create data generators for training and testing
    # train_datagen = ImageDataGenerator(rescale=1./255)
    test_datagen = ImageDataGenerator(rescale=1./255)

    train_generator = train_datagen.flow_from_directory(
        training_data_path,
        target_size=(img_height, img_width),
        batch_size=batch_size,
        class_mode='categorical'  # bc we have two classes
    )

# # Print the class names
# class_names = list(train_generator.class_indices.keys())
# print("Class Names:", class_names)

    test_generator = test_datagen.flow_from_directory(
        testing_data_path,
        target_size=(img_height, img_width),
        batch_size=batch_size,
        class_mode='categorical'
    )

    # Load the pre-trained ResNet-50 model with weights from ImageNet
    base_model = ResNet50(
        include_top=False, # don't want to include the top layer because we will define our own input/output layer
        weights='imagenet',
        input_tensor=None,
        input_shape=(img_height, img_width, 3),
        # pooling=None,
        pooling= 'max',
        classes=2,
    )
    # Freeze only the convolutional layers of the pre-trained model
    for layer in base_model.layers:
        if isinstance(layer, keras.layers.Conv2D):
            layer.trainable = False

            
    # Add custom classification layers on top of ResNet-50
    # these new layers and specifically the 512 neurons are the ones that will be learning the new weights 
    x = Flatten()(base_model.output)
    x = Dense(512, activation='relu')(x)
    x = Dropout(0.5)(x)
    x = Dense(2, activation='softmax')(x)  # Assuming 2 classes: Healthy and Hearing Impaired

    # Create the final model
    model = keras.Model(base_model.input, x)

    # Compile the model
    model.compile(optimizer=Adam(lr=0.001), loss='categorical_crossentropy', metrics=['accuracy'])

    # Train the model
    history = model.fit(train_generator, epochs=100)

    # Train the model and save training history
    history = model.fit(train_generator, epochs=100, verbose=0)

    # Save training loss values to a file
    losses_filename = f'pretrained_losses_fold_{fold_number}.txt'
    with open(losses_filename, 'w') as losses_file:
        losses_file.write("Epoch\tTraining Loss\tTraining Accuracy\n")
        for epoch in range(len(history.history['loss'])):
            losses_file.write(f"{epoch + 1}\t{history.history['loss'][epoch]}\t{history.history['accuracy'][epoch]}\n")

    # Evaluate the model on the testing data
    test_loss, test_acc = model.evaluate(test_generator)
    print(f"\nFold {fold_number} - Test Accuracy: {test_acc}")

    # Get true labels and predicted labels
    predictions = model.predict(test_generator)
    predicted_labels = np.argmax(predictions, axis=1)
    true_labels = test_generator.classes

    # Calculate precision, recall, and f1-score
    precision, recall, f1_score, _ = precision_recall_fscore_support(true_labels, predicted_labels, average='weighted')

    # Save classification results to a file
    results_filename = f'pretrained_classification_results_fold_{fold_number}.txt'
    with open(results_filename, 'w') as results_file:
        results_file.write("Image Name\tTrue Label\tPredicted Label\n")
        for i in range(len(test_generator.filenames)):
            image_name = os.path.basename(test_generator.filenames[i])
            true_label = true_labels[i]
            predicted_label = predicted_labels[i]
            results_file.write(f"{image_name}\t{true_label}\t{predicted_label}\n")

    # Save metrics to a text file
    metrics_filename = f'pretrained_classification_metrics_fold_{fold_number}.txt'
    with open(metrics_filename, 'w') as file:
        file.write(f'Test Accuracy: {test_acc}\n')
        file.write(f'Precision: {precision}\n')
        file.write(f'Recall: {recall}\n')
        file.write(f'F1 Score: {f1_score}\n')

2024-01-28 10:58:50.522522: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-01-28 10:58:50.528493: I external/local_tsl/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2024-01-28 10:58:50.622286: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-01-28 10:58:50.622362: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-01-28 10:58:50.625246: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to

2024-01-28 10:58:52.514737: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT


Found 1440 images belonging to 2 classes.


Found 320 images belonging to 2 classes.


2024-01-28 10:58:54.190546: W tensorflow/core/common_runtime/gpu/gpu_device.cc:2256] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


...

 7/10 [====================>.........] - ETA: 0s

 8/10 [=======================>......] - ETA: 0s

 9/10 [==========================>...] - ETA: 0s

10/10 [==============================] - ETA: 0s

10/10 [==============================] - 5s 305ms/step
